# Initial Orbit Determination with Gauss Method

Gauss initial orbit determination algorithm is given with this code. An initial orbit is determined from three angles.

*Reference: Vallado, D., Fundamentals of Astrodynamics and Applications*

In [1]:
#initialize orekit and JVM
import orekit
orekit.initVM()

from orekit.pyhelpers import setup_orekit_curdir, absolutedate_to_datetime
setup_orekit_curdir()

from org.orekit.frames import FramesFactory, TopocentricFrame
from org.orekit.estimation.measurements import GroundStation, ObservableSatellite
from org.orekit.estimation.measurements import AngularRaDec
from org.orekit.bodies import OneAxisEllipsoid, GeodeticPoint, CelestialBodyFactory
from org.orekit.estimation.iod import IodLambert, IodGibbs
from org.orekit.time import TimeScalesFactory, AbsoluteDate, DateComponents, TimeComponents
from org.orekit.utils import IERSConventions, Constants, PVCoordinates, PVCoordinatesProvider, AbsolutePVCoordinates
from org.hipparchus.geometry.euclidean.threed import Vector3D, SphericalCoordinates
from org.orekit.data import DataProvidersManager, ZipJarCrawler
from org.orekit.orbits import KeplerianOrbit, CartesianOrbit, PositionAngle, OrbitType
from org.orekit.propagation.analytical.tle import TLE, TLEPropagator
from org.orekit.propagation import SpacecraftState

from math import radians, pi, degrees, sin, cos, sqrt, acos
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

First call the frames and time scales to be used in the code and create Earth body.

In [2]:
UTC = TimeScalesFactory.getUTC()                               # Define UTC time scale.
ECI = FramesFactory.getEME2000()                               # Define ECI reference frame.
GCRF = FramesFactory.getGCRF()
ICRF = FramesFactory.getICRF()
ECEF = FramesFactory.getITRF(IERSConventions.IERS_2010, True)  # Define ECEF reference frame.
TEME = FramesFactory.getTEME()                                 # Define TEME reference frame. 
ITRF = ECEF

R_earth  = Constants.WGS84_EARTH_EQUATORIAL_RADIUS             # Radius of earth
Mu_earth = Constants.WGS84_EARTH_MU                            # Gravitational parameter of earth
f_earth  = Constants.WGS84_EARTH_FLATTENING                    # Earth flattening value

earth = OneAxisEllipsoid(R_earth, f_earth, ITRF)               # Create earth here.

Coordinates of the ground station that made the observations and its frame is entered below.

In [3]:
# Define the ground station in geodetic coordinates.
latitude = radians(40.0)
longitude = radians(-110.0)
altitude = 2000.0

# Frame of the ground station is given as Topocentric Frame.
station_coord = GeodeticPoint(latitude, longitude, altitude)
station_frame = TopocentricFrame(earth, station_coord, "Vallado")

# Create the ground station.
ground_station = GroundStation(station_frame)

# Create the observable satellite object, name it 1 as default
obs_sat = ObservableSatellite(1) 

### Gauss Algorithm

Gauss IOD algorithm accepts three observation angles and their respective observation dates as the input.

In [4]:
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~Three seperate observations~~~~~~~~~~~~~~~~~~~~~~~~~
date1  = AbsoluteDate(2012, 8, 20, 11, 40, 28.0, UTC)
ra1    = radians(0.9399130)
dec1   = radians(18.667717)

date2  = AbsoluteDate(2012, 8, 20, 11, 48, 28.0, UTC)
ra2    = radians(45.025748)
dec2   = radians(35.664741)

date3  = AbsoluteDate(2012, 8, 20, 11, 52, 28.0, UTC)
ra3    = radians(67.886655)
dec3   = radians(36.996583)

sigma  = [1.0, 1.0]
baseW  = [1.0, 1.0]

In [5]:
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~ First Observation ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
raDec1 = AngularRaDec(ground_station, ECI, date1, [ra1, dec1], 
                      sigma, baseW, obs_sat)
LOS1   = np.array([[cos(raDec1.getObservedValue()[1]) * cos(raDec1.getObservedValue()[0])],
                   [cos(raDec1.getObservedValue()[1]) * sin(raDec1.getObservedValue()[0])],
                   [sin(raDec1.getObservedValue()[1])]])

ground_station1_ECI = station_frame.getPVCoordinates(date1, ECI).getPosition()    
pos1 = np.array([[ground_station1_ECI.getX()], 
                 [ground_station1_ECI.getY()], 
                 [ground_station1_ECI.getZ()]])

#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~ Second Observation ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
raDec2 = AngularRaDec(ground_station, ECI, date2, [ra2, dec2], 
                      sigma, baseW, obs_sat)
LOS2   = np.array([[cos(raDec2.getObservedValue()[1]) * cos(raDec2.getObservedValue()[0])],
                   [cos(raDec2.getObservedValue()[1]) * sin(raDec2.getObservedValue()[0])],
                   [sin(raDec2.getObservedValue()[1])]])

ground_station2_ECI = station_frame.getPVCoordinates(date2, ECI).getPosition()    
pos2 = np.array([[ground_station2_ECI.getX()], 
                 [ground_station2_ECI.getY()], 
                 [ground_station2_ECI.getZ()]])

#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~ Third Observation ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
raDec3 = AngularRaDec(ground_station, ECI, date3, [ra3, dec3], 
                      sigma, baseW, obs_sat)
LOS3   = np.array([[cos(raDec3.getObservedValue()[1]) * cos(raDec3.getObservedValue()[0])],
                   [cos(raDec3.getObservedValue()[1]) * sin(raDec3.getObservedValue()[0])],
                   [sin(raDec3.getObservedValue()[1])]])

ground_station3_ECI = station_frame.getPVCoordinates(date3, ECI).getPosition()    
pos3 = np.array([[ground_station3_ECI.getX()], 
                 [ground_station3_ECI.getY()], 
                 [ground_station3_ECI.getZ()]])

#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
obs     = list([raDec1, raDec2, raDec3])
LOS     = np.hstack((LOS1, LOS2, LOS3))
LOS_inv = np.linalg.inv(LOS)
R_site  = np.hstack((pos1, pos2, pos3))


# R_site is overwrited here
R_site  = np.array([[4054880.1594,  3956223.5179,  3905072.3452], 
                    [2748194.4767,  2888232.0864,  2956934.5902],
                    [4074236.1653,  4074363.4118,  4074429.3009]])

R_site_df = pd.DataFrame({'1st Observation': [R_site[0][0], R_site[1][0], R_site[2][0]],
                          '2nd Observation': [R_site[0][1], R_site[1][1], R_site[2][1]],
                          '3rd Observation': [R_site[0][2], R_site[1][2], R_site[2][2]]}, 
                           index = ['X (m)', 'Y (m)', 'Z (m)'])
R_site_df.index.name = 'R in ECI'
display(R_site_df)


tau1 = obs[0].getDate().durationFrom(obs[1].getDate())   # [sec]
tau3 = obs[2].getDate().durationFrom(obs[1].getDate())   # [sec]

a1   = tau3/(tau3 - tau1)
a1_u = tau3*((tau3 - tau1)**2 - tau3**2) / (6*(tau3 - tau1))
a3   = -tau1/(tau3 - tau1)
a3_u = -tau1*((tau3 - tau1)**2 - tau1**2) / (6*(tau3 - tau1))

M = np.matmul(LOS_inv, R_site)

d1 = M[1][0]*a1 - M[1][1] + M[1][2]*a3
d2 = M[1][0]*a1_u + M[1][2]*a3_u
C  = np.dot(LOS[:,1], R_site[:,1])

# print("\nd1: ",d1)
# print("d2: ",d2)
# print("C: ",C)

1st Observation  2nd Observation  3rd Observation
R in ECI                                                   
X (m)        4.054880e+06     3.956224e+06     3.905072e+06
Y (m)        2.748194e+06     2.888232e+06     2.956935e+06
Z (m)        4.074236e+06     4.074363e+06     4.074429e+06

In [6]:
#### Create an 8th degree polynomial in r_2
P = list(range(9))

P[0] = 1                                                   # 8th
P[1] = 0                                                   # 7th
P[2] = -(d1**2 + 2*C*d1 + np.linalg.norm(R_site[:,1])**2)  # 6th
P[3] = 0                                                   # 5th
P[4] = 0                                                   # 4th
P[5] = -2*Mu_earth*(C*d2 + d1*d2)                          # 3rd
P[6] = 0                                                   # 2nd
P[7] = 0                                                   # 1st
P[8] = -Mu_earth**2 * d2**2                                # 0th

roots = np.roots(P)

PosRoots = []
for item in roots:
    if np.isreal(item) and item > 0:
        PosRoots.append(item)

if len(PosRoots) == 1:
    r2 = PosRoots[0].real
else:
    pass

# Below value allows you to find an initial estimate of the slant-range values, 
# which ends Gauss’s part of the solution. First, find the three c_i coefficients.
u = Mu_earth / r2**3

c1 = -(-a1 -a1_u*u)
c2 = -1
c3 = -(-a3 -a3_u*u)

# Now, determine the initial guess of the slant ranges. Be sure to multiply the matrices out first.
B = np.matmul(M, np.array([[-c1], [-c2], [-c3]]))

A = np.identity(3)
A[0,0] = c1
A[1,1] = c2
A[2,2] = c3

slant_ranges = np.linalg.solve(A,B)
slant_ranges_df = pd.DataFrame(slant_ranges, 
                               index = ['1st Observation', '2nd Observation', '3rd Observation'])
slant_ranges_df.columns = ['Slant Range (m)']
display(slant_ranges_df)

position = []
for i in range(3):
    pos = slant_ranges[i]*LOS[:, i] + R_site[:, i]
    pos = np.transpose(pos) 
    position = np.concatenate((position, pos))

position = position.reshape((3, 3))
position_df = pd.DataFrame({'1st Observation': [position[0][0], position[1][0], position[2][0]],
                            '2nd Observation': [position[0][1], position[1][1], position[2][1]],
                            '3rd Observation': [position[0][2], position[1][2], position[2][2]]}, 
                            index = ['X (m)', 'Y (m)', 'Z (m)'])

display(position_df)

Slant Range (m)
1st Observation     4.169739e+06
2nd Observation     4.104960e+06
3rd Observation     4.546684e+06

1st Observation  2nd Observation  3rd Observation
X (m)     8.004721e+06     2.812996e+06     5.408883e+06
Y (m)     6.313396e+06     5.247524e+06     6.467725e+06
Z (m)     5.272041e+06     6.321125e+06     6.810475e+06

### Refinement of Gauss IOD 

Lagrange coefficients *f* and *g* are calculated below to find the velocity vector *v_2*

In [7]:
##################################################################
###### Curtis Algorithm 5.5 steps 9-13 continued.
###### We find v2 vector from Gauss slant range solution.
##################################################################

f1 = 1 - (0.5*(Mu_earth/np.linalg.norm(position[1,:])**3)*tau1**2)
f3 = 1 - (0.5*(Mu_earth/np.linalg.norm(position[1,:])**3)*tau3**2)
g1 = tau1 - ((1/6)*(Mu_earth/np.linalg.norm(position[1,:])**3)*tau1**3)
g3 = tau3 - ((1/6)*(Mu_earth/np.linalg.norm(position[1,:])**3)*tau3**3)

v2 = (1/(f1*g3 - f3*g1))*(-f3*position[0,:] + f1*position[2,:])

# Position vector p2 is taken from the result of Gauss IOD.
p2 = Vector3D(float(position[1,0]), float(position[1,1]), float(position[1,2]))
v2 = Vector3D(float(v2[0]), float(v2[1]), float(v2[2]))
PVcoord = PVCoordinates(p2, v2)

cartesianOrbit = CartesianOrbit(PVcoord, ECI, date2, Mu_earth)
keplerElements = OrbitType.KEPLERIAN.convertType(SpacecraftState(cartesianOrbit, 1.0).getOrbit())

print('\033[1m'+'\nFor second observation: \n'+'\033[0m', keplerElements)
##################################################################
##################################################################


For second observation: 
 Keplerian parameters: {a: 1.1551587766670126E7; e: 0.17197301329729583; i: 40.01833895033979; pa: 9.209390300950984; raan: -30.035070012778785; v: 65.02799363451854;}


### Comparison with Lambert IOD

In [8]:
p1 = Vector3D([float(position[0][0]) , float(position[0][1]), float(position[0][2])])
p2 = Vector3D([float(position[1][0]), float(position[1][1]), float(position[1][2])])

lambert = IodLambert(Mu_earth)

estimated_orbit = lambert.estimate(ECI, True, 0, p1, date1, p2, date2);
print(estimated_orbit)

Keplerian parameters: {a: 1.155165547020492E7; e: 0.16702085040879452; i: 40.01833895033979; pa: 10.714481785226273; raan: -30.03507001277881; v: 46.00209994930481;}


### Comparison with Gibbs 

In [9]:
# Test extracted from "Fundamentals of astrodynamics & applications", 
# D. Vallado, 3rd ed., chp. Initial Orbit Determination, Example 7-3, p.457

posR1 = Vector3D(float(position[0][0]), float(position[0][1]), float(position[0][2])) # Position of first observation.
posR2 = Vector3D(float(position[1][0]), float(position[1][1]), float(position[1][2])) # Position of second observation.
posR3 = Vector3D(float(position[2][0]), float(position[2][1]), float(position[2][2])) # Position of third observation.

# Corresponding observation dates are gathered from Gauss method previously.

# Initialization of Gibbs IOD Method
gibbs = IodGibbs(Mu_earth)

# Gibbs IOD orbit estimation
estimated_orbit = gibbs.estimate(ECI, posR1, date1, posR2, date2, posR3, date3)
print('\033[1m'+'\nKepler elements:\n '+'\033[0m', estimated_orbit)
print('\033[1m'+'\nPV coordinates:\n '+'\033[0m', estimated_orbit.getPVCoordinates())

"""
# Comparison with the reference data (cf. Vallado)
velR2 = Vector3D(0.0, 5531.148, -5191.806)
abs_error = estimated_orbit.getPVCoordinates().getVelocity().getNorm() - velR2.getNorm()
print("\n Absolute error between velocities: ", abs_error)
"""


Kepler elements:
  Keplerian parameters: {a: 1.2128172456637757E7; e: 0.19784731921826476; i: 40.0183389503398; pa: 19.789250992198685; raan: -30.035070012778696; v: 54.44813294327076;}

PV coordinates:
  {2012-08-20T11:48:28.000, P(6313395.577554378, 5247523.66541471, 6467724.7809437), V(-4185.517646991476, 4788.532965378182, 1721.7326586324739), A(-2.204480053055134, -1.8323042024277234, -2.258367956370617)}


'\n# Comparison with the reference data (cf. Vallado)\nvelR2 = Vector3D(0.0, 5531.148, -5191.806)\nabs_error = estimated_orbit.getPVCoordinates().getVelocity().getNorm() - velR2.getNorm()\nprint("\n Absolute error between velocities: ", abs_error)\n'